In [ ]:
import selfies as sf
from tokenizers import Tokenizer
from tokenizers.models import WordLevel
from tokenizers.pre_tokenizers import Split
from tokenizers.processors import TemplateProcessing
from tokenizers.trainers import WordLevelTrainer
from tqdm import tqdm

In [ ]:
with open("./train.txt") as f:
    smiles = [line.strip() for line in f]

selfies = []
for smile in tqdm(smiles):
    try:
        selfies.append(sf.encoder(smile))
    except:
        pass

In [ ]:
tokenizer = Tokenizer(WordLevel(unk_token="<UNK>"))

tokenizer.pre_tokenizer = Split(
    pattern="]", 
    behavior="merged_with_previous"
)

trainer = WordLevelTrainer(
    special_tokens=["<CLS>", "<EOS>", "<PAD>", "<UNK>"]
)

tokenizer.train_from_iterator(selfies, trainer=trainer)

In [ ]:
tokenizer.post_processor = TemplateProcessing(
    single="<CLS> $A <EOS>",
    special_tokens=[
        ("<CLS>", tokenizer.token_to_id("<CLS>")),
        ("<EOS>", tokenizer.token_to_id("<EOS>")),
    ],
)

tokenizer.enable_padding(
    direction="right",
    pad_id=tokenizer.token_to_id("<PAD>"),
    pad_token="<PAD>",
)

In [ ]:
tokenizer.save("./tokenizer.json")